#Background

In HW2, we implemented the standard Needleman-Wunsch algorithm for global sequence alignment.
Identifying sequence homology is invaluable for gaining insight into evolutionary relationships and functional similarities of different genes.
However, sequence homology has limitations.
Protein **structures** are conserved throughout evolutionary time much longer than **sequences**[<sup>1</sup>](https://doi.org/10.1002/prot.22458), so it is possible that two functionally (and structurally) similar protein structures will have a poor sequence alignment, leading to their functional similarity being missed by a sequence homology database search.

Structure-based search may provide a more sensitive method to identify functionally related proteins.
With the advent of accurate protein structure prediction tools like [AlphaFold](https://doi.org/10.1038/s41586-021-03819-2), structural information about any protein sequence is readily available for anyone to search through.
Whereas sequence alignment maximizes an alignment score by strategically inserting gaps in correct places, [structural alignment](https://en.wikipedia.org/wiki/Structural_alignment) does the same by strategically superimposing the 3D atomic coordinates of each amino acid in two protein structures.

![structural](https://www.researchgate.net/publication/51150635/figure/fig11/AS:325001434681352@1454497788152/The-structural-alignment-of-two-topologically-different-yet-structurally-similar.png)

However, structural alignment is super slow.
Structural alignment does not exhibit optimal substructure like sequence alignment does, so alignments must be computed via iterative stochastic optimization instead of dynamic programming.
It would take [TM-align](https://doi.org/10.1093/nar/gki524), a structural alignment tool, 10,000 years to compute do an all by all comparison of 100 million protein structures on a 1,000-core cluster, whereas the same task using sequence alignment would take roughly a week on the same cluster[<sup>2</sup>](https://doi.org/10.1038/s41587-023-01773-0).

[Foldseek](https://doi.org/10.1038/s41587-023-01773-0) is a recently published method for fast structure-based search of proteins.
Foldseek cleverly avoids structural-alignment by reducing the problem down to a sequence alignment task.
This reduction boils down to describing tertiary amino acid interactions within proteins as sequences over a structural alphabet (more on this below).
![foldseek](https://raw.githubusercontent.com/danielchang2002/5481_supplementary/main/foldseek.png)

In this quick demo notebook, we will explore a simple case study of two protein sequences that exhibit very similar structures and function but very different sequences.
We will demonstrate how structure comparison can reveal insights into their relationships that sequence homology fails to do.
We will also demonstrate how using the Foldseek 3Di mapping can reduce the expensive problem of structure-based search down to a sequence alignment.



# Lets download and prepare the data!

We will be looking at two human proteins, [ubiquitin](https://www.uniprot.org/uniprotkb/P0CG48/entry) and [SUMO](https://www.uniprot.org/uniprotkb/P55854/entry).
Briefly skim the blurb that uniprot gives about their function.  
While they have various differences in their function, they both are involved in post-translational modification, likely via a similar mechanism.


In [1]:
UBIQUITIN_PDB = "1d3z"
SUMO_PDB = "1u4a"

UBIQUITIN_UNIPROT = "P0CG48"
SUMO_UNIPROT = "P55854"

In [2]:
# download their experimentally solved structural information (A chain)

! wget "https://www.ebi.ac.uk/pdbe/entry-files/download/pdb"$UBIQUITIN_PDB".ent"
! wget "https://www.ebi.ac.uk/pdbe/entry-files/download/pdb"$SUMO_PDB".ent"

--2023-10-29 22:30:40--  https://www.ebi.ac.uk/pdbe/entry-files/download/pdb1d3z.ent
Resolving www.ebi.ac.uk (www.ebi.ac.uk)... 193.62.193.80
Connecting to www.ebi.ac.uk (www.ebi.ac.uk)|193.62.193.80|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1015740 (992K) [text/plain]
Saving to: ‘pdb1d3z.ent’

pdb1d3z.ent         100%[===================>] 991.93K   400KB/s    in 2.5s    

2023-10-29 22:30:43 (400 KB/s) - ‘pdb1d3z.ent’ saved [1015740/1015740]

--2023-10-29 22:30:43--  https://www.ebi.ac.uk/pdbe/entry-files/download/pdb1u4a.ent
Resolving www.ebi.ac.uk (www.ebi.ac.uk)... 193.62.193.80
Connecting to www.ebi.ac.uk (www.ebi.ac.uk)|193.62.193.80|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 2058048 (2.0M) [text/plain]
Saving to: ‘pdb1u4a.ent’

pdb1u4a.ent         100%[===================>]   1.96M   608KB/s    in 3.3s    

2023-10-29 22:30:47 (608 KB/s) - ‘pdb1u4a.ent’ saved [2058048/2058048]



In [3]:
# download their sequences

! wget "https://rest.uniprot.org/uniprotkb/"$UBIQUITIN_UNIPROT".fasta"
! wget "https://rest.uniprot.org/uniprotkb/"$SUMO_UNIPROT".fasta"

--2023-10-29 22:30:47--  https://rest.uniprot.org/uniprotkb/P0CG48.fasta
Resolving rest.uniprot.org (rest.uniprot.org)... 193.62.193.81
Connecting to rest.uniprot.org (rest.uniprot.org)|193.62.193.81|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 775 [text/plain]
Saving to: ‘P0CG48.fasta’

P0CG48.fasta        100%[===================>]     775  --.-KB/s    in 0s      

2023-10-29 22:30:48 (811 MB/s) - ‘P0CG48.fasta’ saved [775/775]

--2023-10-29 22:30:48--  https://rest.uniprot.org/uniprotkb/P55854.fasta
Resolving rest.uniprot.org (rest.uniprot.org)... 193.62.193.81
Connecting to rest.uniprot.org (rest.uniprot.org)|193.62.193.81|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 206 [text/plain]
Saving to: ‘P55854.fasta’

P55854.fasta        100%[===================>]     206  --.-KB/s    in 0s      

2023-10-29 22:30:48 (126 MB/s) - ‘P55854.fasta’ saved [206/206]



In [4]:
# read and select the subsequence corresponding to their A chain

with open(f"{UBIQUITIN_UNIPROT}.fasta") as f:
  lines = f.readlines()
  ubiquitin_seq = "".join([li.strip() for li in lines[1:]])[:76]

with open(f"{SUMO_UNIPROT}.fasta") as f:
  lines = f.readlines()
  SUMO_seq = "".join([li.strip() for li in lines[1:]])[16:92]

print(len(ubiquitin_seq), len(SUMO_seq))
print(ubiquitin_seq)
print(SUMO_seq)

76 76
MQIFVKTLTGKTITLEVEPSDTIENVKAKIQDKEGIPPDQQRLIFAGKQLEDGRTLSDYNIQKESTLHLVLRLRGG
INLKVAGQDGSVVQFKIKRHTPLSKLMKAYCERQGLSMRQIRFRFDGQPINETDTPAQLEMEDEDTIDVFQQQTGG


# Let's visualize the structures!

In [ ]:
! pip install py3Dmol
import py3Dmol

In [ ]:
def show_pdb(fname):
  with open(fname) as ifile:
      system = "".join([x for x in ifile])

  view = py3Dmol.view(width=400, height=300)
  view.addModelsAsFrames(system)
  view.setStyle({'model': -1}, {"cartoon": {'color': 'spectrum'}})
  view.zoomTo()
  view.show()

In [ ]:
show_pdb(f"pdb{UBIQUITIN_PDB}.ent")
show_pdb(f"pdb{SUMO_PDB}.ent")

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

Try clicking and dragging the protein structures to rotate their views. You should be able to see that they are slightly different, but look very similar!

# Let's compare the sequences!

### TODO: finish this function! Use the alignment code you wrote for HW2

In [ ]:
import numpy as np

def align(query, ref, gap_penalty, mismatch_penalty,
    match_score, ignore_outer_gaps, start_gap_penalty):
    """
    Given a query and reference sequence and scores to assign to gaps and
    (mis)matches, return the aligned sequences, alignment score, and a
    string to help with visualizing the alignment
    """

    query_aligned, visual, ref_aligned, align_score = "", "", "", 0

    #-----------------------------Start code here---------------------------------

    # Implement the alignment algorithm!

    #-----------------------------End code here---------------------------------


    return query_aligned, visual, ref_aligned, align_score

In [ ]:
q, v, r, a = align(ubiquitin_seq, SUMO_seq, -2, -1, 1, False, 0)

100%|██████████| 76/76 [00:00<00:00, 2144.10it/s]


In [ ]:
print(a)
print(q)
print(v)
print(r)

-51.0
MQIFVKTLTG_KTITLEVEPSDTIENVKAKIQDKEGIPPDQQRLIFAGKQLEDGRTLSDYNIQKESTLHLVLRLRGG
xxxx|xxxx| xxxxxxxxxxxxxxxx|| xxxxx|xxxx|x|xx|x|xxxxxxx|xxxxxxxx|x|xxxxxxxx||
INLKVAGQDGSVVQFKIKRHTPLSKLMKA_YCERQGLSMRQIRFRFDGQPINETDTPAQLEMEDEDTIDVFQQQTGG


If your alignment code is correct, you should get a score of -51.
Hm, it looks we don't produce a strong sequence alignment.

# Structural alignment

Let's see what happens if we use TMalign to produce a structural alignment.

In [ ]:
# install TMalign

! git clone https://github.com/kad-ecoli/TMalign.git
%cd TMalign
! make
%cd ../

Cloning into 'TMalign'...
remote: Enumerating objects: 813, done.
remote: Counting objects: 100% (76/76), done.
remote: Compressing objects: 100% (50/50), done.
remote: Total 813 (delta 48), reused 50 (delta 26), pack-reused 737
Receiving objects: 100% (813/813), 1.05 MiB | 4.39 MiB/s, done.
Resolving deltas: 100% (574/574), done.
/content/TMalign
g++ -O3 -ffast-math TMalign.cpp -o TMalign -static
g++ -O3 -ffast-math TMscore.cpp -o TMscore -static
g++ -O3 -ffast-math MMalign.cpp -o MMalign -static
g++ -O3 -ffast-math se.cpp -o se -static
g++ -O3 -ffast-math pdb2xyz.cpp -o pdb2xyz -static
g++ -O3 -ffast-math xyz_sfetch.cpp -o xyz_sfetch -static
g++ -O3 -ffast-math pdb2fasta.cpp -o pdb2fasta -static
g++ -O3 -ffast-math pdb2ss.cpp -o pdb2ss -static
g++ -O3 -ffast-math NWalign.cpp -o NWalign -static
/content


In [ ]:
! ./TMalign/TMalign "pdb"$UBIQUITIN_PDB".ent" "pdb"$SUMO_PDB".ent"


 **********************************************************************
 * TM-align (Version 20210520): protein and RNA structure alignment   *
 * References: Y Zhang, J Skolnick. Nucl Acids Res 33, 2302-9 (2005)  *
 *             S Gong, C Zhang, Y Zhang. Bioinformatics, bz282 (2019) *
 * Please email comments and suggestions to yangzhanglab@umich.edu    *
 **********************************************************************

Name of Structure_1: pdb1d3z.ent (to be superimposed onto Structure_2)
Name of Structure_2: pdb1u4a.ent
Length of Structure_1: 76 residues
Length of Structure_2: 79 residues

Aligned length= 73, RMSD=   1.89, Seq_ID=n_identical/n_aligned= 0.151
TM-score= 0.77652 (normalized by length of Structure_1: L=76, d0=3.08)
TM-score= 0.75259 (normalized by length of Structure_2: L=79, d0=3.16)
(You should use TM-score normalized by length of the reference structure)

(":" denotes residue pairs of d < 5.0 Angstrom, "." denotes other aligned residues)
---MQIFVKTLTGKTITLEV

Looks like a strong structural alignment was achieved! 73 out of 76 residue pairs had a distance of less than 5 Angstrom in the alignment.

# Approximating structural alignment

Structural alignment is expensive.
While the small structures took only a millisecond to structurally align, the time cost scales poorly.
Lets see how we can get an efficient approximation of structural alignment by reducing the problem to a sequence alignment!

Foldseek converts a protein structure into what they call a "3Di" (3D interaction) sequence, where each element $i$ in the 3Di sequence describes the tertiary interactions that amino acid $i$ has w/ its neighbors (left in fig. below).

In a nutshell, amino acid residues are mapped to structural state letters.
This is done by extracting a feature vector of each residue based on its (local) physical arrangment with respect to local neighbors (middle diagram in fig. below).
These feature vectors are then fed into a [VQ-VAE](https://doi.org/10.48550/arXiv.1711.00937) (right diagram in fig. below), which essentially perform non-linear clustering.

![3di](https://raw.githubusercontent.com/danielchang2002/5481_supplementary/main/foldseek_3di.png)

The output of this process is we obtain a structural state sequence of same length as the amino acid sequence!
Below, we will use precomputed 3di sequences of our case study proteins, and perform sequence alignment to observe their structural similarity!

In [5]:
# download ubiquitin and SUMO 3di sequences. These were obtained by extracting the features and throwing them into the aforementioned VQ-VAE

! wget https://raw.githubusercontent.com/danielchang2002/5481_supplementary/main/remote_homologs_3Di.fasta

--2023-10-29 22:30:48--  https://raw.githubusercontent.com/danielchang2002/5481_supplementary/main/remote_homologs_3Di.fasta
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 165 [text/plain]
Saving to: ‘remote_homologs_3Di.fasta’

remote_homologs_3Di 100%[===================>]     165  --.-KB/s    in 0s      

2023-10-29 22:30:49 (9.81 MB/s) - ‘remote_homologs_3Di.fasta’ saved [165/165]



In [6]:
with open("remote_homologs_3Di.fasta") as f:
  lines = f.readlines()
  ubiquitin_seq_3Di = lines[1].strip()
  SUMO_seq_3Di = lines[3].strip()

print(len(ubiquitin_seq_3Di))
print(len(SUMO_seq_3Di))
print(ubiquitin_seq_3Di)
print(SUMO_seq_3Di)

76
76
DKEWEAEPVGDIDIDDDDQADFPLNVLVVVCVVPVAPSVFKWKDFPRDTGDRVGGNVVVVADPHGYIYIDGDDPPD
AWEWEAEPVRDTDTDTDDLQDFLLVVVCVVCVVPPHDPPWKWKAFPNDTDDRRDRVVSNVDRHDGYIYIYTDDDDD


Foldseek also defines a substitution matrix for variable mismatch penalties, which were trained by comparing a dataset of TM-align (gold-standard) alignments w/ 3Di sequences.

In [7]:
# download substitution matrix
! wget https://raw.githubusercontent.com/danielchang2002/5481_supplementary/main/3di_substitution.csv

--2023-10-29 22:30:49--  https://raw.githubusercontent.com/danielchang2002/5481_supplementary/main/3di_substitution.csv
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.110.133, 185.199.111.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1310 (1.3K) [text/plain]
Saving to: ‘3di_substitution.csv’

3di_substitution.cs 100%[===================>]   1.28K  --.-KB/s    in 0s      

2023-10-29 22:30:49 (84.5 MB/s) - ‘3di_substitution.csv’ saved [1310/1310]



In [8]:
import pandas as pd
substitution_matrix = pd.read_csv("3di_substitution.csv")
substitution_matrix

A   C  D   E  F  G  H   I   K   L  ...   N  P   Q  R   S   T   V   W   Y  \
A   6  -3  1   2  3 -2 -2  -7  -3  -3  ...  -5 -1   1 -4  -7  -5  -6   0  -2   
C  -3   6 -2  -8 -5 -4 -4 -12 -13   1  ...   0  0   1 -1   0  -8   1  -7  -9   
D   1  -2  4  -3  0  1  1  -3  -5  -4  ...  -2  1  -1 -1  -4  -2  -3  -2  -2   
E   2  -8 -3   9 -2 -7 -4 -12 -10  -7  ...  -8 -6  -3 -8 -10 -10 -13  -6  -3   
F   3  -5  0  -2  7 -3 -3  -5   1  -3  ...  -5 -2   2 -5  -8  -3  -7   4  -4   
G  -2  -4  1  -7 -3  6  3   0  -7  -7  ...  -2 -2  -4  3  -3   4  -6  -4  -2   
H  -2  -4  1  -4 -3  3  6  -4  -7  -6  ...   0 -1  -3  1  -3  -1  -5  -5   3   
I  -7 -12 -3 -12 -5  0 -4   8  -5 -11  ...  -7 -6  -6 -3  -9   6 -12  -5  -8   
K  -3 -13 -5 -10  1 -7 -7  -5   9 -11  ... -12 -6  -5 -9 -14  -5 -15   5  -8   
L  -3   1 -4  -7 -3 -7 -6 -11 -11   6  ...  -3 -2   2 -4  -4  -9   0  -8  -9   
M -10 -14 -5 -17 -9 -1 -6   7  -8 -16  ...  -9 -9 -10 -5 -10   3 -16  -6  -9   
N  -5   0 -2  -8 -5 -2  0  -7 -12  -3  ...   7  0  -2  2   3  -4   0  -8  -5   
P  -1   0  1  -6 -2 -2 -1  -6  -6  -2  ...   0  4   0  0  -2  -4   0  -4  -5   
Q   1   1 -1  -3  2 -4 -3  -6  -5   2  ...  -2  0   5 -2  -4  -5  -1  -2  -5   
R  -4  -1 -1  -8 -5  3  1  -3  -9  -4  ...   2  0  -2  6   2   0  -1  -6  -3   
S  -7   0 -4 -10 -8 -3 -3  -9 -14  -4  ...   3 -2  -4  2   6  -6   0 -11  -9   
T  -5  -8 -2 -10 -3  4 -1   6  -5  -9  ...  -4 -4  -5  0  -6   8  -9  -5  -5   
V  -6   1 -3 -13 -7 -6 -5 -12 -15   0  ...   0  0  -1 -1   0  -9   3 -10 -11   
W   0  -7 -2  -6  4 -4 -5  -5   5  -8  ...  -8 -4  -2 -6 -11  -5 -10   8  -6   
Y  -2  -9 -2  -3 -4 -2  3  -8  -8  -9  ...  -5 -5  -5 -3  -9  -5 -11  -6   9   
X   0   0  0   0  0  0  0   0   0   0  ...   0  0   0  0   0   0   0   0   0   

   X  
A  0  
C  0  
D  0  
E  0  
F  0  
G  0  
H  0  
I  0  
K  0  
L  0  
M  0  
N  0  
P  0  
Q  0  
R  0  
S  0  
T  0  
V  0  
W  0  
Y  0  
X  0  

[21 rows x 21 columns]

### TODO: finish this function! Modify the alignment code you wrote for HW2 to handle variable substitution scores

In [10]:
import numpy as np

def align_substitution(query, ref, gap_penalty, substitution_matrix,
    ignore_outer_gaps, start_gap_penalty):
    """
    Given a query and reference sequence and scores to assign to gaps and
    (mis)matches, return the aligned sequences, alignment score, and a
    string to help with visualizing the alignment
    """

    query_aligned, visual, ref_aligned, align_score = "", "", "", 0

    #-----------------------------Start code here---------------------------------

    # Implement the alignment algorithm w/ variable substitution scores!

    #-----------------------------End code here---------------------------------


    return query_aligned, visual, ref_aligned, align_score

In [16]:
q, v, r, a = align_substitution(ubiquitin_seq_3Di, SUMO_seq_3Di, -2, substitution_matrix, False, 0)

100%|██████████| 76/76 [00:00<00:00, 263.27it/s]


In [17]:
print(a)
print(q)
print(v)
print(r)

272.0
DKEWEAEPVGDIDIDDDDQADFPLNVLVVVCVVPV_APSVFKWKDFPRDTGDRVGGNVV_VVADPH_GYIYIDGDDPPD
xx|||||||x|x|x|x||xx||x|x|xx||||||x x| xx|||x||x||x|| xxx|| x| |x| |||||xx||xx|
AWEWEAEPVRDTDTDTDDLQDFLLVVVCVVCVVPPHDP_PWKWKAFPNDTDDR_RDRVVSNV_DRHDGYIYIYTDDDDD


Huzzah! If your new alignment function is correct, you should get an alignment score of 272.